In [1]:
!pip install --upgrade requests branca six jinja2 numpy chardet idna urllib3 certifi MarkupSafe
!conda install -c conda-forge folium --yes
!conda install -c conda-forge geopy --yes
!pip install bs4
!pip install uszipcode
!pip install tqdm

#import all the libraries
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
import requests
import random
from sklearn.cluster import KMeans
from pandas.io.json import json_normalize
import folium
#from folium.plugins import MiniMap
from geopy.geocoders import Nominatim
import json
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn import metrics
from PIL import Image
import matplotlib.patches as mpatches
import types
from botocore.client import Config
import ibm_boto3
from bs4 import BeautifulSoup
from uszipcode import SearchEngine
import geopy
from geopy.extra.rate_limiter import RateLimiter
import tqdm
from tqdm._tqdm_notebook import tqdm_notebook

print('Libraries imported')

     |████████████████████████████████| 71kB 5.0MB/s eta 0:00:01
     |████████████████████████████████| 133kB 12.2MB/s eta 0:00:01
     |████████████████████████████████| 14.5MB 797kB/s  eta 0:00:01
Requirement already up-to-date: chardet in /opt/conda/envs/Python36/lib/python3.6/site-packages (3.0.4)
     |████████████████████████████████| 61kB 3.3MB/s  eta 0:00:01
     |████████████████████████████████| 133kB 19.4MB/s eta 0:00:01
Requirement already up-to-date: certifi in /opt/conda/envs/Python36/lib/python3.6/site-packages (2020.6.20)
ERROR: tensorflow 1.13.1 requires tensorboard<1.14.0,>=1.13.0, which is not installed.
ERROR: ibm-cos-sdk-core 2.4.3 has requirement urllib3<1.25,>=1.20, but you'll have urllib3 1.25.10 which is incompatible.
ERROR: botocore 1.12.82 has requirement urllib3<1.25,>=1.20, but you'll have urllib3 1.25.10 which is incompatible.
ERROR: autoai-libs 1.10.5 has requirement pandas>=0.24.2, but you'll have pandas 0.24.1 which is incompatible.
  Found existing in

In [3]:


#New York Geographical Data on Neighborhoods/Boroughs
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

#Load data
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
    
#Take a look at the data
#newyork_data

#the relevant data is in the features key, which is basically a list of neighborhoods
NY_data = newyork_data['features']

# Transform the NY Data into a Pandas dataframe
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
NYdf = pd.DataFrame(columns=column_names)

# Make sure the columns are correct
NYdf
NY_data[0]

for data in NY_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    NYdf = NYdf.append({'Borough': borough,
                        'Neighborhood': neighborhood_name,
                        'Latitude': neighborhood_lat,
                        'Longitude': neighborhood_lon}, ignore_index=True)
    
    #Take only the neighborhoods from Manhattan
NYdf =NYdf[NYdf['Borough'] == 'Manhattan'].reset_index(drop=True)
NYdf.head(10)

Data downloaded!


Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688
5  Manhattan      Manhattanville  40.816934 -73.957385
6  Manhattan      Central Harlem  40.815976 -73.943211
7  Manhattan         East Harlem  40.792249 -73.944182
8  Manhattan     Upper East Side  40.775639 -73.960508
9  Manhattan           Yorkville  40.775930 -73.947118

In [23]:
NYdf.shape

(40, 4)

In [4]:

NYaddress = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
NYlocation = geolocator.geocode(NYaddress)
NYlatitude = NYlocation.latitude
NYlongitude = NYlocation.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(NYlatitude, NYlongitude))

The geograpical coordinate of New York City are 40.7896239, -73.9598939.


In [24]:
NYdf

Borough         Neighborhood   Latitude  Longitude
0   Manhattan          Marble Hill  40.876551 -73.910660
1   Manhattan            Chinatown  40.715618 -73.994279
2   Manhattan   Washington Heights  40.851903 -73.936900
3   Manhattan               Inwood  40.867684 -73.921210
4   Manhattan     Hamilton Heights  40.823604 -73.949688
5   Manhattan       Manhattanville  40.816934 -73.957385
6   Manhattan       Central Harlem  40.815976 -73.943211
7   Manhattan          East Harlem  40.792249 -73.944182
8   Manhattan      Upper East Side  40.775639 -73.960508
9   Manhattan            Yorkville  40.775930 -73.947118
10  Manhattan           Lenox Hill  40.768113 -73.958860
11  Manhattan     Roosevelt Island  40.762160 -73.949168
12  Manhattan      Upper West Side  40.787658 -73.977059
13  Manhattan       Lincoln Square  40.773529 -73.985338
14  Manhattan              Clinton  40.759101 -73.996119
15  Manhattan              Midtown  40.754691 -73.981669
16  Manhattan          Murray Hill  40.748303 -73.978332
17  Manhattan              Chelsea  40.744035 -74.003116
18  Manhattan    Greenwich Village  40.726933 -73.999914
19  Manhattan         East Village  40.727847 -73.982226
20  Manhattan      Lower East Side  40.717807 -73.980890
21  Manhattan              Tribeca  40.721522 -74.010683
22  Manhattan         Little Italy  40.719324 -73.997305
23  Manhattan                 Soho  40.722184 -74.000657
24  Manhattan         West Village  40.734434 -74.006180
25  Manhattan     Manhattan Valley  40.797307 -73.964286
26  Manhattan  Morningside Heights  40.808000 -73.963896
27  Manhattan             Gramercy  40.737210 -73.981376
28  Manhattan    Battery Park City  40.711932 -74.016869
29  Manhattan   Financial District  40.707107 -74.010665
30  Manhattan        Carnegie Hill  40.782683 -73.953256
31  Manhattan                 Noho  40.723259 -73.988434
32  Manhattan         Civic Center  40.715229 -74.005415
33  Manhattan        Midtown South  40.748510 -73.988713
34  Manhattan         Sutton Place  40.760280 -73.963556
35  Manhattan           Turtle Bay  40.752042 -73.967708
36  Manhattan           Tudor City  40.746917 -73.971219
37  Manhattan      Stuyvesant Town  40.731000 -73.974052
38  Manhattan             Flatiron  40.739673 -73.990947
39  Manhattan         Hudson Yards  40.756658 -74.000111

In [ ]:
#Check here because we are supposed to combine Toronto and NY
df_org = df.copy()
df_org.drop(index=['Bob', 'Dave', 'Frank'], inplace=True)


NYdf=NYdf.copy()
NYdf.drop(index=[ ])
#TorNY_df = NYdf.append(tmp, True).reset_index(drop = True)
#pd.set_option('max_rows', 6)
#TorNY_df

In [9]:
#renaming TorNY_df to NYdf - Troubleshoot
map_tony = folium.Map(location=[NYlatitude, NYlongitude], zoom_start=12, width='100%', height='100%')

for lat, lng, borough, neighborhood in zip(NYdf['Latitude'], NYdf['Longitude'], NYdf['Borough'], NYdf['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_tony)
map_tony

In [ ]:
#mini map?

In [10]:
# The code was removed by Watson Studio for sharing.

CMPLNT_NUM  ADDR_PCT_CD   BORO_NM CMPLNT_FR_DT    YEAR  Unnamed: 5  \
0   466502077           75  BROOKLYN   2020-03-30  2020.0         NaN   
1   303191835           77  BROOKLYN   2020-03-28  2020.0         NaN   
2   735488557           43     BRONX   2020-03-29  2020.0         NaN   
3   315962428           40     BRONX   2020-03-29  2020.0         NaN   
4   165437868          114    QUEENS   2020-03-27  2020.0         NaN   

   Unnamed: 6 CMPLNT_FR_TM CMPLNT_TO_DT CMPLNT_TO_TM  ... SUSP_SEX  \
0         NaN     17:30:00    3/31/2020      6:53:00  ...      NaN   
1         NaN     19:30:00    3/28/2020     20:30:00  ...        M   
2         NaN     14:10:00          NaN          NaN  ...      NaN   
3         NaN      7:10:00    3/29/2020      7:16:00  ...        M   
4         NaN     13:15:00    3/27/2020     14:00:00  ...      NaN   

  TRANSIT_DISTRICT  VIC_AGE_GROUP        VIC_RACE VIC_SEX  X_COORD_CD  \
0              NaN          25-44           BLACK       M     1018496   
1              NaN            <18         UNKNOWN       F     1003606   
2              NaN        UNKNOWN         UNKNOWN       D     1019853   
3              NaN          25-44  WHITE HISPANIC       F     1007236   
4              NaN          45-64           BLACK       F     1002018   

  Y_COORD_CD   Latitude  Longitude                                   Lat_Lon  
0     178657  40.656991 -73.876574   (40.65699087900003, -73.87657444799999)  
1     185050  40.674583 -73.930222   (40.67458330800008, -73.93022154099998)  
2     241853  40.830443 -73.871349        (40.83044253800006, -73.871349147)  
3     237260  40.817878 -73.916957  (40.817877907000025, -73.91695668199996)  
4     213258  40.752011 -73.935872   (40.75201086000004, -73.93587196099996)  

[5 rows x 38 columns]

In [11]:
NYCrime.columns

Index(['CMPLNT_NUM', 'ADDR_PCT_CD', 'BORO_NM', 'CMPLNT_FR_DT', 'YEAR',
       'Unnamed: 5', 'Unnamed: 6', 'CMPLNT_FR_TM', 'CMPLNT_TO_DT',
       'CMPLNT_TO_TM', 'CRM_ATPT_CPTD_CD', 'HADEVELOPT', 'HOUSING_PSA',
       'JURISDICTION_CODE', 'JURIS_DESC', 'KY_CD', 'LAW_CAT_CD',
       'LOC_OF_OCCUR_DESC', 'OFNS_DESC', 'PARKS_NM', 'PATROL_BORO', 'PD_CD',
       'PD_DESC', 'PREM_TYP_DESC', 'RPT_DT', 'STATION_NAME', 'SUSP_AGE_GROUP',
       'SUSP_RACE', 'SUSP_SEX', 'TRANSIT_DISTRICT', 'VIC_AGE_GROUP',
       'VIC_RACE', 'VIC_SEX', 'X_COORD_CD', 'Y_COORD_CD', 'Latitude',
       'Longitude', 'Lat_Lon'],
      dtype='object')

In [12]:

# Clean the NYCrime Data
#Drop columns that are not needed

NYCrime.drop(['CMPLNT_NUM','YEAR', 'Unnamed: 5', 'Unnamed: 6', 'CMPLNT_FR_TM', 'CMPLNT_TO_DT',
       'CMPLNT_TO_TM', 'CRM_ATPT_CPTD_CD', 'HADEVELOPT',
       'HOUSING_PSA', 'JURISDICTION_CODE', 'JURIS_DESC', 'KY_CD', 'LAW_CAT_CD',
       'LOC_OF_OCCUR_DESC', 'RPT_DT', 'PARKS_NM', 'PATROL_BORO', 'PD_CD',
       'PD_DESC', 'PREM_TYP_DESC','KY_CD', 'PD_CD', 'PD_DESC',
       'CRM_ATPT_CPTD_CD', 'LAW_CAT_CD', 'JURIS_DESC',
       'LOC_OF_OCCUR_DESC', 'PREM_TYP_DESC', 'PARKS_NM',
       'HADEVELOPT', 'STATION_NAME', 'SUSP_AGE_GROUP',
       'SUSP_RACE', 'SUSP_SEX', 'TRANSIT_DISTRICT', 'VIC_AGE_GROUP',
       'VIC_RACE', 'VIC_SEX', 'X_COORD_CD', 'Y_COORD_CD'
             ], axis=1, inplace=True)

#Rename columns names for consistency across all dataframes

NYCrime.rename(columns ={'ADDR_PCT_CD' : 'Precinct Number',
                         'CMPLNT_FR_DT': 'Occurrence Year', 
                         'OFNS_DESC' : 'MCI', 
                         'BORO_NM' : 'Borough',
                         'Latitude' : 'Lat', 
                         'Longitude' : 'Long', 
                         'Lat_Lon' : 'Coordinates'}, inplace=True)

NYCrime.head(5)

Precinct Number   Borough Occurrence Year                           MCI  \
0               75  BROOKLYN      2020-03-30                 PETIT LARCENY   
1               77  BROOKLYN      2020-03-28                          RAPE   
2               43     BRONX      2020-03-29                 PETIT LARCENY   
3               40     BRONX      2020-03-29                 PETIT LARCENY   
4              114    QUEENS      2020-03-27  ASSAULT 3 & RELATED OFFENSES   

         Lat       Long                               Coordinates  
0  40.656991 -73.876574   (40.65699087900003, -73.87657444799999)  
1  40.674583 -73.930222   (40.67458330800008, -73.93022154099998)  
2  40.830443 -73.871349        (40.83044253800006, -73.871349147)  
3  40.817878 -73.916957  (40.817877907000025, -73.91695668199996)  
4  40.752011 -73.935872   (40.75201086000004, -73.93587196099996)

In [13]:

NYCrime['Occurrence Year'] = pd.to_datetime(NYCrime['Occurrence Year'], format='%Y-%m-%d') #%Y-%m-%d  #%m/%d/%Y

NYCrime.head(5)

Precinct Number   Borough Occurrence Year                           MCI  \
0               75  BROOKLYN      2020-03-30                 PETIT LARCENY   
1               77  BROOKLYN      2020-03-28                          RAPE   
2               43     BRONX      2020-03-29                 PETIT LARCENY   
3               40     BRONX      2020-03-29                 PETIT LARCENY   
4              114    QUEENS      2020-03-27  ASSAULT 3 & RELATED OFFENSES   

         Lat       Long                               Coordinates  
0  40.656991 -73.876574   (40.65699087900003, -73.87657444799999)  
1  40.674583 -73.930222   (40.67458330800008, -73.93022154099998)  
2  40.830443 -73.871349        (40.83044253800006, -73.871349147)  
3  40.817878 -73.916957  (40.817877907000025, -73.91695668199996)  
4  40.752011 -73.935872   (40.75201086000004, -73.93587196099996)

In [14]:

NYCrime['Occurrence Year'] = NYCrime['Occurrence Year'].dt.year 
NYCrime.head(5)

Precinct Number   Borough  Occurrence Year                           MCI  \
0               75  BROOKLYN             2020                 PETIT LARCENY   
1               77  BROOKLYN             2020                          RAPE   
2               43     BRONX             2020                 PETIT LARCENY   
3               40     BRONX             2020                 PETIT LARCENY   
4              114    QUEENS             2020  ASSAULT 3 & RELATED OFFENSES   

         Lat       Long                               Coordinates  
0  40.656991 -73.876574   (40.65699087900003, -73.87657444799999)  
1  40.674583 -73.930222   (40.67458330800008, -73.93022154099998)  
2  40.830443 -73.871349        (40.83044253800006, -73.871349147)  
3  40.817878 -73.916957  (40.817877907000025, -73.91695668199996)  
4  40.752011 -73.935872   (40.75201086000004, -73.93587196099996)

In [15]:

#Isolate to only the year 2019
NYCrime = NYCrime[NYCrime['Occurrence Year'] == 2019].reset_index(drop=True)
NYCrime.head(5)

Precinct Number    Borough  Occurrence Year              MCI        Lat  \
0                5  MANHATTAN             2019       SEX CRIMES  40.716196   
1               81   BROOKLYN             2019             RAPE  40.689616   
2               83   BROOKLYN             2019  DANGEROUS DRUGS  40.690655   
3               40      BRONX             2019    PETIT LARCENY  40.813805   
4               43      BRONX             2019      THEFT-FRAUD  40.815733   

        Long                               Coordinates  
0 -73.997491  (40.716195914000025, -73.99749074599998)  
1 -73.924393  (40.689615497000034, -73.92439311199998)  
2 -73.908043   (40.69065484200007, -73.90804256199993)  
3 -73.929653   (40.81380495100007, -73.92965290199999)  
4 -73.848350  (40.815733075000026, -73.84835004699994)

In [16]:
# Find out the percentage of types of crime in 2019
#calculate the number of occurrences of each MCI
NYCrimePer = pd.DataFrame(NYCrime['MCI'].value_counts().astype(float))
NYCrimePer = NYCrimePer.reset_index()
NYCrimePer.columns = ['MCI', 'Number of Occurrence'] 

#convert to percentages of the total crimes that occurred in 2019
NYCrimePer['Percentage of Occurrence'] = 100*NYCrimePer['Number of Occurrence']/NYCrimePer['Number of Occurrence'].sum()
NYCrimePer.head(5)

MCI  Number of Occurrence  \
0                   PETIT LARCENY                1171.0   
1                   GRAND LARCENY                1104.0   
2                   HARRASSMENT 2                 512.0   
3  CRIMINAL MISCHIEF & RELATED OF                 466.0   
4   OFF. AGNST PUB ORD SENSBLTY &                 339.0   

   Percentage of Occurrence  
0                 22.813170  
1                 21.507890  
2                  9.974674  
3                  9.078512  
4                  6.604325

In [17]:

NYCrimePer.tail(5)

MCI  Number of Occurrence  \
31            ANTICIPATORY OFFENSES                   3.0   
32   INTOXICATED & IMPAIRED DRIVING                   3.0   
33             FRAUDULENT ACCOSTING                   2.0   
34         OFFENSES INVOLVING FRAUD                   2.0   
35  PROSTITUTION & RELATED OFFENSES                   2.0   

    Percentage of Occurrence  
31                  0.058445  
32                  0.058445  
33                  0.038964  
34                  0.038964  
35                  0.038964

In [18]:
#Import and explore the Crime Data
#Import Homicide Data and MCI data  Toronto as separate dataframes... Will combine into a main dataframe later after cleaning
#the MCI Data does not include homicide data, which is why we need to compbine.
 
body = client_e073509e2b4e4fd9ab9d353e029fb9c7.get_object(Bucket='courseraibmcapstone-donotdelete-pr-iibp9ibtexxq7g',Key='Homicide.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )
  
# If you are reading an Excel file into a pandas DataFrame, replace `read_csv` by `read_excel` in the next statement.
TCrime_Homicidedf = pd.read_csv(body)
TCrime_Homicidedf.head()

X          Y  Index_ Event_Unique_ID  Occurrence_year Division  \
0 -79.386620  43.648640     201         1787320             2006      D52   
1 -79.304939  43.715988     202         1470621             2006      D54   
2 -79.304939  43.715988     203         1470621             2006      D54   
3 -79.228691  43.809391     204         1448992             2006      D42   
4 -79.484482  43.649334     205         1945800             2006      D11   

  Homicide_Type           Occurrence_Date  Hood_ID  \
0      Shooting  2006-10-27T04:00:00.000Z       77   
1      Stabbing  2006-11-05T05:00:00.000Z       43   
2      Stabbing  2006-11-05T05:00:00.000Z       43   
3      Shooting  2006-11-14T05:00:00.000Z      132   
4         Other  2006-11-25T05:00:00.000Z       87   

                            Neighbourhood        Lat       Long  ObjectId  
0  Waterfront Communities-The Island (77)  43.648640 -79.386620         1  
1                   Victoria Village (43)  43.715988 -79.304939         2  
2                   Victoria Village (43)  43.715988 -79.304939         3  
3                           Malvern (132)  43.809391 -79.228691         4  
4                  High Park-Swansea (87)  43.649334 -79.484482         5

In [19]:
#visualize data

!wget -q -O 'police_precincts.geojson' https://raw.githubusercontent.com/dwillis/nyc-maps/master/police_precincts.geojson
    
print('Data downloaded!')

Data downloaded!


In [20]:
#import json
file = open('police_precincts.geojson', 'rt')
#print(file.readlines())

NYCrime_geo = json.load(file)

In [21]:
#calculate the total number of incidences per neighborhood
#Lat, Long columns
NY_crime = pd.DataFrame(NYCrime['Precinct Number'].value_counts().astype(float))
NY_crime = NY_crime.reset_index()
NY_crime.columns = ['Precinct Number', 'Number']
NY_crime.head(10)

Precinct Number  Number
0               75   156.0
1               19   155.0
2              113   136.0
3               70   111.0
4              105   110.0
5               67   107.0
6               18   100.0
7               44   100.0
8               14   100.0
9              114    98.0

In [22]:

#create a choropleth map
NYCrime_map = folium.Map(location=[40.7896239, -73.9598939], tiles='openstreetmap')
NYCrime_map.choropleth(
    geo_data = NYCrime_geo,
    name = 'NYC Crime Heat Map',
    data = NY_crime,
    columns = ['Precinct Number', 'Number'],
    key_on = 'feature.properties.Precinct',
    zoome_start = 10,
    fill_color = 'YlOrRd',
    fill_opacity = 0.7,
    line_opacity = 0.2,
    legend_name = 'Crimes in New York City - Manhattan'
)
NYCrime_map

/opt/conda/envs/Python36/lib/python3.6/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
